In [1]:
# ~~~ Imports ~~~
%load_ext autoreload
%autoreload 2
import os
import hydra
import subprocess


from aiflows.backends.api_info import ApiInfo
from aiflows.utils.general_helpers import read_yaml_file, quick_load_api_keys

from aiflows import logging
from aiflows.flow_cache import CACHING_PARAMETERS, clear_cache

from aiflows.utils import serving
from aiflows.workers import run_dispatch_worker_thread
from aiflows.messages import FlowMessage
from aiflows.interfaces import KeyInterface
from aiflows.utils.colink_utils import start_colink_server
from aiflows.workers import run_dispatch_worker_thread

from aiflows import flow_verse



/Users/nicolasbaldwin/opt/miniconda3/envs/mockenv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Defining Functions Which Reproduce The Steps Of The Quick Start Tutorial (no modifications required)

In [2]:
# ~~~ Convenience function that install the dependencies for the Flows in this notebook ~~~
# Normally, you would install the dependencies in your terminal, as necessary. We do it here for you convenience

DEPENDENCIES_DICT = {
    "ChatFlowModule": "aiflows/ChatFlowModule",
    "ReAct": "aiflows/ControllerExecutorFlowModule",
    "ChatInteractiveFlowModule": "aiflows/ChatInteractiveFlowModule",
    "ChatWithDemonstrationsFlowModule": "aiflows/ChatWithDemonstrationsFlowModule",
    "AutoGPTFlowModule": "aiflows/AutoGPTFlowModule",
    "VisionFlowModule": "aiflows/VisionFlowModule",
}

def download_all_flow_dependencies(flow):
    """Download all dependencies for a flow from FlowVerse and pip requirements. 
    
    Note that this is a convenience function for this tutorial and is not meant to work doesn't work for all Flows on FlowVerse.
    
    :param flow: The name of the Flow to download dependencies for
    :type flow: str
    """
    # ~~~ Load Flow dependecies from FlowVerse ~~~
    dependencies = [
        {"url": DEPENDENCIES_DICT[flow], "revision": "main"},
    ]
    flow_verse.sync_dependencies(dependencies)
    
    # path to pip requirements file
    path_to_requirements = os.path.join("flow_modules" ,DEPENDENCIES_DICT[flow], "pip_requirements.txt")

    # download dependencies
    subprocess.check_call(["pip", "install", "-r", path_to_requirements], stdout=subprocess.DEVNULL)

# ~~~ Load Flow dependecies from FlowVerse and pip requirments ~~~
for key in DEPENDENCIES_DICT.keys():
    download_all_flow_dependencies(key)

[2024-03-22 16:23:07,873][aiflows.flow_verse.loading:775][INFO] - [<interactive>] started to sync flow module dependencies to /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/examples/quick_start/flow_modules...
[2024-03-22 16:23:08,226][aiflows.flow_verse.loading:608][INFO] - aiflows/ChatFlowModule:main already synced, skip
[2024-03-22 16:23:08,228][aiflows.flow_verse.loading:825][INFO] - [<interactive>] finished syncing


[2024-03-22 16:23:16,119][aiflows.flow_verse.loading:775][INFO] - [<interactive>] started to sync flow module dependencies to /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/examples/quick_start/flow_modules...
[2024-03-22 16:23:16,316][aiflows.flow_verse.loading:608][INFO] - aiflows/ControllerExecutorFlowModule:main already synced, skip
[2024-03-22 16:23:16,321][aiflows.flow_verse.loading:825][INFO] - [<interactive>] finished syncing


[2024-03-22 16:23:23,791][aiflows.flow_verse.loading:775][INFO] - [<interactive>] 

## Start Local Colink Server & Serve all flows

In [3]:
cl = start_colink_server()

In [4]:
#serve all flows
for flow_module in DEPENDENCIES_DICT.keys():
    flow_url = DEPENDENCIES_DICT[flow_module]

    # ~~~ Load Flow config ~~~
    path_to_config = os.path.join( "flow_modules" ,flow_url, "demo.yaml")
    cfg = read_yaml_file(path_to_config)
    flow_path = cfg["_target_"].split(".")
    flow_class_name = ".".join(flow_path[:-1])
    flow_endpoint = flow_path[-2]

    serving.recursive_serve_flow(
        cl = cl,
        flow_class_name=flow_class_name,
        flow_endpoint=flow_endpoint
    )   

[2024-03-22 16:23:56,024][aiflows.utils.serve_utils:116][INFO] - Started serving flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow at flows:ChatAtomicFlow.
[2024-03-22 16:23:56,027][aiflows.utils.serve_utils:117][INFO] - dispatch_point: coflows_dispatch
[2024-03-22 16:23:56,028][aiflows.utils.serve_utils:118][INFO] - parallel_dispatch: False
[2024-03-22 16:23:56,031][aiflows.utils.serve_utils:119][INFO] - singleton: False

[2024-03-22 16:23:56,059][aiflows.flow_verse.loading:775][INFO] - [flow_modules.aiflows.ControllerExecutorFlowModule] started to sync flow module dependencies to /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/examples/quick_start/flow_modules...
[2024-03-22 16:23:56,266][aiflows.flow_verse.loading:608][INFO] - aiflows/ChatFlowModule:main already synced, skip
[2024-03-22 16:23:56,341][aiflows.flow_verse.loading:825][INFO] - [flow_modules.aiflows.ControllerExecutorFlowModule] finished syncing


[2024-03-22 16:23:56,450][aiflows.base_flows.abs

In [5]:
#4. ~~~~~Start A Worker Thread~~~~~
run_dispatch_worker_thread(cl)

[2024-03-22 16:24:03,692][aiflows.workers.dispatch_worker:235][INFO] - Dispatch worker started in attached thread.
[2024-03-22 16:24:03,711][aiflows.workers.dispatch_worker:236][INFO] - dispatch_point: coflows_dispatch


In [6]:
def run_flow(flow, data, api_information):
    """Runs inference of the requested flow
    
    :param flow: The name of the flow to run
    :type flow: str
    :param data: The input data to the flow
    :type data: dict
    :param api_information: The api information for the flow
    :type api_information: ApiInfo
    """
    
    flow_url = DEPENDENCIES_DICT[flow]
    # ~~~ Load Flow config ~~~
    path_to_config = os.path.join( "flow_modules" ,flow_url, "demo.yaml")
    
    cfg = read_yaml_file(path_to_config)
    
    quick_load_api_keys(cfg, api_information, key="api_infos")
    
    flow_path = cfg["_target_"].split(".")

    flow_endpoint = flow_path[-2]
    
    #~~~~~Mount the flow and get its proxy~~~~~~
    proxy_flow = serving.get_flow_instance(
        cl=cl,
        flow_endpoint=flow_endpoint,
        user_id="local",
        config_overrides = cfg
    )
    
    #~~~ Run inference ~~~
    message = proxy_flow.package_input_message(data)
    
    future = proxy_flow.get_reply_future(message)
    
    reply_data = future.get_data()
    
    serving.delete_flow_instance(cl,proxy_flow.get_instance_id())
    # ~~~ Print the output ~~~
    print("~~~~~~Reply~~~~~~")
    print(reply_data)
    
    

### Setting you API Information

Set your API information here (copy-paste it)

In [7]:

#OpenAI backend
api_key = os.getenv("OPENAI_API_KEY") # copy paste your api key here
api_information = [ApiInfo(backend_used="openai", api_key=api_key)]

# Azure backend
# api_key = "" # copy paste your api key here
# api_base = "" # copy paste your api base here
# api_version = "" #copypase your api base here
# api_information = ApiInfo(backend_used = "azure",
#                           api_base =api_base,
#                           api_key = api_version,
#                           api_version =  api_version )

### Pick a Flow, some data and run it!

Set the `Flow` and `data` values, then run the cell! Examples for each flow from the FlowVerse are provided in the cell bellow. Uncomment the flow and data you wish to run. Here is the list of flows available for you to run:

* [ChatFlowModule](https://huggingface.co/aiflows/ChatFlowModule)

* [ReAct](https://huggingface.co/aiflows/ControllerExecutorFlowModule)

* [AutoGPTFlowModule](https://huggingface.co/aiflows/AutoGPTFlowModule)

* [ChatInteractiveFlowModule](https://huggingface.co/aiflows/ChatInteractiveFlowModule)

* [ChatWithDemonstrationsFlowModule](https://huggingface.co/aiflows/ChatWithDemonstrationsFlowModule)

* [VisionFlowModule](https://huggingface.co/aiflows/VisionFlowModule)


In [8]:
# Example for a simple chatbot
# [ChatFlowModule](https://huggingface.co/aiflows/ChatFlowModule)

flow = "ChatFlowModule"  
data = {"id": 0, "question": "Who was the NBA champion in 2023?"} 
run_flow(flow, data, api_information)

[2024-03-22 16:24:03,997][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:24:04,049][aiflows.utils.serve_utils:336][INFO] - Mounted d3d973e1-ca9c-472e-9db7-2c325b4888cc at flows:ChatAtomicFlow:mounts:local:d3d973e1-ca9c-472e-9db7-2c325b4888cc
[2024-03-22 16:24:04,050][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.


[2024-03-22 16:24:04,106][aiflows.base_flows.abstract:95][DEBUG] - Flow Proxy_ChatAtomicFlow instantiated with the following parameters:


CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy_ChatAtomicFlow                                                                                       
├── description
│   └── Proxy of ChatAtomicFlow                                                                                    
├── user_id
│   └── local                                                                                                      
├── flow_id
│   └── d3d973e1-ca9c-472e-9db7-2c325b4888cc                                                                       
└── flow_endpoint
    └── ChatAtomicFlow                                                                                             

[2024-03-22 16:24:04,377][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `Proxy_ChatAtomicFlow` --> `unknown` ~~~
{
    "message_id": "329d1445-6944-47dc-9005-eaf6bd75d5a8",
    "created_at": "2024-03-22 15:24:04.377180000",
    "message_type": "FlowMessage",
    "created_by": "Proxy_ChatAtomicFlow",
    "data": {
        "id": 0,
        "question": "Who was the NBA champion in 2023?"
    },
    "src_flow_id": "d3d973e1-ca9c-472e-9db7-2c325b4888cc",
    "reply_data": {
        "mode": "no_reply"
    },
    "src_flow": "Proxy_ChatAtomicFlow",
    "dst_flow": "unknown",
    "input_message_id": "329d1445-6944-47dc-9005-eaf6bd75d5a8",
    "is_reply": false,
    "user_id": "023215d6d023f802cc4d5a91d06aad92f44c33a70ab8f0802995ac74381732dcab"
}
[2024-03-22 16:24:04,422][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ ResetMessageNamespaceOnly (UpdateMessage_NamespaceReset): `Proxy_ChatAtomicFlow` ~~~
{
    "message_id": "1a4c60fb-c4ea-49ad-80cd-b1141b2bdcf6",
    "created_at": 

[2024-03-22 16:24:04,433][aiflows.workers.dispatch_worker:119][INFO] - 
~~~ Dispatch task ~~~
[2024-03-22 16:24:04,450][aiflows.workers.dispatch_worker:161][INFO] - flow_endpoint: ChatAtomicFlow
[2024-03-22 16:24:04,451][aiflows.workers.dispatch_worker:162][INFO] - flow_id: d3d973e1-ca9c-472e-9db7-2c325b4888cc
[2024-03-22 16:24:04,452][aiflows.workers.dispatch_worker:163][INFO] - owner_id: local
[2024-03-22 16:24:04,453][aiflows.workers.dispatch_worker:164][INFO] - message_paths: ['push_tasks:2dc03a5b-771c-4e16-9a4e-ddf0defbdf50:msg']
[2024-03-22 16:24:04,454][aiflows.workers.dispatch_worker:165][INFO] - parallel_dispatch: False

[2024-03-22 16:24:04,502][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:24:04,546][aiflows.base_flows.abstract:95][DEBUG] - Flow SimpleQA_Flow instantiated with the following parameters:
[2024-03-22 16:24:04,589][aifl

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── True                                                                                                       
├── _target_
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow.instantiate_from_default_config                         
├── name
│   └── SimpleQA_Flow                                                                                              
├── description
│   └── A flow that answers questions.                                                                             
├── n_api_retries
│   └── 6                                                                                                          
├── wait_time_between_retries
│   └── 20                                                                                                         
├── system_name
│   └── system                                                                                                     
├── user_name
│   └── user                                                                                                       
├── assistant_name
│   └── assistant                                                                                                  
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── system_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'You are a helpful chatbot that truthfully 
├── init_human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'Answer the following question: {{question}
├── human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': '{{query}}', 'input_variables': ['query']} 
├── input_interface_initialized
│   └── ['query']                                                                                                  
├── query_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt'}                                                        
├── previous_messages
│   └── {'first_k': None, 'last_k': None}                                                                          
├── output_interface
│   └── ['api_output']                                                                                             
├── input_interface_non_initialized
│   └── ['question']                                                                                               
└── flow_id
    └── d3d973e1-ca9c-472e-9db7-2c325b4888cc                                                                       

[2024-03-22 16:24:06,074][aiflows.utils.serve_utils:242][INFO] - Deleted flow instance d3d973e1-ca9c-472e-9db7-2c325b4888cc.
~~~~~~Reply~~~~~~
{'api_output': "I'm sorry, but as an AI, I cannot predict the future. I can only provide information up to the present day."}


In [9]:
# Example for ReAct (the simplest instance of a ControllerExecutorFlowModule)
flow = "ReAct"
data = {"id": 0, "goal": "Who was the NBA champion in 2023?"}
run_flow(flow, data, api_information)

[2024-03-22 16:24:12,470][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/CompositeFlow.yaml.
[2024-03-22 16:24:12,512][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:24:12,574][aiflows.utils.serve_utils:336][INFO] - Mounted 11d47af4-de30-4c49-9d72-02ed429ab08c at flows:ControllerAtomicFlow:mounts:local:11d47af4-de30-4c49-9d72-02ed429ab08c
[2024-03-22 16:24:12,590][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:24:12,632][aiflows.utils.serve_utils:336][INFO] - Mounted dc78d263-5315-478d-9688-88cc1d20bbd1 at flows:WikiSearchAtomicFlow:mounts:local:dc78d263-5315-478d-9688-88cc1d20bbd1
[2024-03-22

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy_ControllerExecutorFlow                                                                               
├── description
│   └── Proxy of ControllerExecutorFlow                                                                            
├── user_id
│   └── local                                                                                                      
├── flow_id
│   └── 8824af81-74a4-4103-a80c-c2d2ac5806be                                                                       
└── flow_endpoint
    └── ControllerExecutorFlow                                                                                     

[2024-03-22 16:24:12,952][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `Proxy_ControllerExecutorFlow` --> `unknown` ~~~
{
    "message_id": "a52e7e35-c3e2-4ea4-8a21-40fc327fe7c0",
    "created_at": "2024-03-22 15:24:12.951910000",
    "message_type": "FlowMessage",
    "created_by": "Proxy_ControllerExecutorFlow",
    "data": {
        "id": 0,
        "goal": "Who was the NBA champion in 2023?"
    },
    "src_flow_id": "8824af81-74a4-4103-a80c-c2d2ac5806be",
    "reply_data": {
        "mode": "no_reply"
    },
    "src_flow": "Proxy_ControllerExecutorFlow",
    "dst_flow": "unknown",
    "input_message_id": "a52e7e35-c3e2-4ea4-8a21-40fc327fe7c0",
    "is_reply": false,
    "user_id": "023215d6d023f802cc4d5a91d06aad92f44c33a70ab8f0802995ac74381732dcab"
}
[2024-03-22 16:24:12,976][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ ResetMessageNamespaceOnly (UpdateMessage_NamespaceReset): `Proxy_ControllerExecutorFlow` ~~~
{
    "message_id": "1b02fb52-7b91-46bd-8908-d2e2f

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy Controller                                                                                           
├── description
│   └── A flow that acts as a proxy for the controller.                                                            
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerAtomicFlow                                     
├── flow_endpoint
│   └── ControllerAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── commands
│   └── {'finish': {'description': 'Signal that the objective has been satisfied, and returns the answer to the use
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
└── flow_id
    └── 11d47af4-de30-4c49-9d72-02ed429ab08c                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.WikiSearchAtomicFlow                                     
├── flow_endpoint
│   └── WikiSearchAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── name
│   └── WikiSearchAtomicFlow                                                                                       
├── description
│   └── A flow that searches Wikipedia for information.                                                            
└── flow_id
    └── dc78d263-5315-478d-9688-88cc1d20bbd1                                                                       

...

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── True                                                                                                       
├── _target_
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerAtomicFlow.instantiate_from_default_config     
├── name
│   └── Proxy Controller                                                                                           
├── description
│   └── A flow that acts as a proxy for the controller.                                                            
├── n_api_retries
│   └── 6                                                                                                          
├── wait_time_between_retries
│   └── 20                                                                                                         
├── system_name
│   └── system                                                                                                     
├── user_name
│   └── user                                                                                                       
├── assistant_name
│   └── assistant                                                                                                  
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── system_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'You are a smart AI assistant. \n\nYour dec
├── init_human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'Here is the goal you need to achieve:\n{{g
├── human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'Here is the goal you need to achieve:\n{{g
├── input_interface_initialized
│   └── ['observation', 'goal']                                                                                    
├── query_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt'}                                                        
├── previous_messages
│   └── {'first_k': None, 'last_k': None}                                                                          
├── output_interface
│   └── ['thought', 'reasoning', 'plan', 'criticism', 'speak', 'command', 'command_args']                          
├── input_interface_non_initialized
│   └── ['goal']                                                                                                   
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerAtomicFlow                                     
├── commands
│   └── {'finish': {'description': 'Signal that the objective has been satisfied, and returns the answer to the use
└── flow_id
    └── 11d47af4-de30-4c49-9d72-02ed429ab08c                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy Controller                                                                                           
├── description
│   └── A flow that acts as a proxy for the controller.                                                            
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerAtomicFlow                                     
├── flow_endpoint
│   └── ControllerAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── commands
│   └── {'finish': {'description': 'Signal that the objective has been satisfied, and returns the answer to the use
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
└── flow_id
    └── 11d47af4-de30-4c49-9d72-02ed429ab08c                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.WikiSearchAtomicFlow                                     
├── flow_endpoint
│   └── WikiSearchAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── name
│   └── WikiSearchAtomicFlow                                                                                       
├── description
│   └── A flow that searches Wikipedia for information.                                                            
└── flow_id
    └── dc78d263-5315-478d-9688-88cc1d20bbd1                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── CtrlEx                                                                                                     
├── description
│   └── ControllerExecutor (i.e., MRKL, ReAct) interaction implementation with Flows that approaches the problem so
├── max_rounds
│   └── 30                                                                                                         
├── _target_
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerExecutorFlow.instantiate_from_default_config   
├── input_interface
│   └── ['goal']                                                                                                   
├── output_interface
│   └── ['answer', 'status']                                                                                       
├── subflows_config
│   └── {'Controller': {'name': 'Proxy Controller', 'description': 'A flow that acts as a proxy for the controller.
└── flow_id
    └── 8824af81-74a4-4103-a80c-c2d2ac5806be                                                                       

[2024-03-22 16:24:29,736][aiflows.utils.serve_utils:242][INFO] - Deleted flow instance 8824af81-74a4-4103-a80c-c2d2ac5806be.
~~~~~~Reply~~~~~~
{'answer': 'Denver Nuggets', 'status': 'finished'}


In [13]:
# Example for AutoGPTFlowModule
flow = "AutoGPTFlowModule"
data = {"id": 0, "goal": "Who was the NBA champion in 2023?"}
run_flow(flow, data, api_information)

[2024-03-22 16:14:11,708][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/CompositeFlow.yaml.
[2024-03-22 16:14:11,946][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:14:12,056][aiflows.utils.serve_utils:336][INFO] - Mounted c0a3fd86-33f3-439b-94e7-5a0e3f8ef362 at flows:ControllerAtomicFlow:mounts:local:c0a3fd86-33f3-439b-94e7-5a0e3f8ef362
[2024-03-22 16:14:12,105][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:14:12,181][aiflows.utils.serve_utils:336][INFO] - Mounted 45f60ca5-29a2-4d22-a7da-b7b51e6520fa at flows:WikiSearchAtomicFlow:mounts:local:45f60ca5-29a2-4d22-a7da-b7b51e6520fa
[2024-03-22

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy_AutoGPTFlow                                                                                          
├── description
│   └── Proxy of AutoGPTFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── flow_id
│   └── 790d570f-0d83-4b32-a494-334f64bd8793                                                                       
└── flow_endpoint
    └── AutoGPTFlow                                                                                                

[2024-03-22 16:14:12,537][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `Proxy_AutoGPTFlow` --> `unknown` ~~~
{
    "message_id": "a8282b6c-ca76-4d35-8fd1-a880883420a9",
    "created_at": "2024-03-22 15:14:12.537694000",
    "message_type": "FlowMessage",
    "created_by": "Proxy_AutoGPTFlow",
    "data": {
        "id": 0,
        "goal": "Who was the NBA champion in 2023?"
    },
    "src_flow_id": "790d570f-0d83-4b32-a494-334f64bd8793",
    "reply_data": {
        "mode": "no_reply"
    },
    "src_flow": "Proxy_AutoGPTFlow",
    "dst_flow": "unknown",
    "input_message_id": "a8282b6c-ca76-4d35-8fd1-a880883420a9",
    "is_reply": false,
    "user_id": "02268c9af0d23501d04a455bc7865b7d6cb64ff4c0ba817efb3aea1afda4a936fc"
}
[2024-03-22 16:14:12,568][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ ResetMessageNamespaceOnly (UpdateMessage_NamespaceReset): `Proxy_AutoGPTFlow` ~~~
{
    "message_id": "b731327e-723d-45a4-8f26-73d4208571d1",
    "created_at": "2024-03-22 15:1

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy Controller                                                                                           
├── description
│   └── A flow that acts as a proxy for the controller.                                                            
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerAtomicFlow                                     
├── flow_endpoint
│   └── ControllerAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── commands
│   └── {'finish': {'description': 'Signal that the objective has been satisfied, and returns the answer to the use
├── finish
│   └── {'description': 'Signal that the objective has been satisfied, and returns the answer to the user.', 'input
├── human_message_prompt_template
│   └── {'template': 'Here is the response to your last action:\n{{observation}}\nHere is the feedback from the use
├── input_interface_initialized
│   └── ['observation', 'human_feedback']                                                                          
├── backend
│   └── {'api_infos': [{'_target_': 'aiflows.backends.api_info.ApiInfo', 'backend_used': 'openai', 'api_key': 'sk-Q
├── previous_messages
│   └── {'last_k': 1, 'first_k': 2}                                                                                
└── flow_id
    └── c0a3fd86-33f3-439b-94e7-5a0e3f8ef362                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.WikiSearchAtomicFlow                                     
├── flow_endpoint
│   └── WikiSearchAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── name
│   └── proxy WikiSearchAtomicFlow                                                                                 
├── description
│   └── A flow that searches Wikipedia for information.                                                            
└── flow_id
    └── 45f60ca5-29a2-4d22-a7da-b7b51e6520fa                                                                       

...

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.WikiSearchAtomicFlow                                     
├── flow_endpoint
│   └── WikiSearchAtomicFlow                                                                                       
├── user_id
│   └── local                                                                                                      
├── name
│   └── proxy WikiSearchAtomicFlow                                                                                 
├── description
│   └── A flow that searches Wikipedia for information.                                                            
└── flow_id
    └── 45f60ca5-29a2-4d22-a7da-b7b51e6520fa                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy HumanFeedbackFlow                                                                                    
├── description
│   └── A proxy flow that requests feedback from a human.                                                          
├── flow_class_name
│   └── flow_modules.aiflows.HumanStandardInputFlowModule.HumanStandardInputFlow                                   
├── user_id
│   └── local                                                                                                      
├── flow_endpoint
│   └── HumanStandardInputFlow                                                                                     
├── request_multi_line_input_flag
│   └── False                                                                                                      
├── query_message_prompt_template
│   └── {'template': 'Please provide feedback on the last step. To quit type: "q".\n\nRelevant information:\n== Goa
├── input_interface_initialized
│   └── ['goal', 'command', 'command_args', 'observation']                                                         
└── flow_id
    └── bcb3bca5-8c7d-4c3c-b864-7766230c3c3c                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── n_results
│   └── 2                                                                                                          
├── flow_class_name
│   └── flow_modules.aiflows.VectorStoreFlowModule.ChromaDBFlow                                                    
├── flow_endpoint
│   └── MemoryFlow                                                                                                 
├── user_id
│   └── local                                                                                                      
├── name
│   └── MemoryFlow                                                                                                 
├── description
│   └── A flow that acts as a proxy for the memory.                                                                
├── backend
│   └── {'model_name': 'none', 'api_infos': [{'_target_': 'aiflows.backends.api_info.ApiInfo', 'backend_used': 'ope
└── flow_id
    └── 3cb7b6c7-8229-48a5-8c23-8e0f1da93bbc                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── AutoGPTFlow                                                                                                
├── description
│   └── An example implementation of AutoGPT with Flows.                                                           
├── max_rounds
│   └── 30                                                                                                         
├── _target_
│   └── flow_modules.aiflows.ControllerExecutorFlowModule.ControllerExecutorFlow.instantiate_from_default_config   
├── input_interface
│   └── ['goal']                                                                                                   
├── output_interface
│   └── ['answer', 'status']                                                                                       
├── subflows_config
│   └── {'Controller': {'name': 'Proxy Controller', 'description': 'A flow that acts as a proxy for the controller.
├── early_exit_key
│   └── EARLY_EXIT                                                                                                 
└── flow_id
    └── 790d570f-0d83-4b32-a494-334f64bd8793                                                                       

[2024-03-22 16:17:19,904][aiflows.utils.serve_utils:242][INFO] - Deleted flow instance 790d570f-0d83-4b32-a494-334f64bd8793.
~~~~~~Reply~~~~~~
{'answer': 'Denver Nuggets', 'status': 'finished'}


In [11]:
# Example for ChatInteractiveFlowModule
flow = "ChatInteractiveFlowModule"
data = {"id": 0,  "query": "I want to ask you a few questions"} # you will be able to ask questions once it is running
run_dispatch_worker_thread(cl)
run_flow(flow, data, api_information)

[2024-03-22 16:24:52,333][aiflows.workers.dispatch_worker:235][INFO] - Dispatch worker started in attached thread.
[2024-03-22 16:24:52,336][aiflows.workers.dispatch_worker:236][INFO] - dispatch_point: coflows_dispatch
[2024-03-22 16:24:52,380][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/CompositeFlow.yaml.
[2024-03-22 16:24:52,420][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.


[2024-03-22 16:24:52,464][aiflows.utils.serve_utils:336][INFO] - Mounted c8c19619-89f9-4bce-8f49-b3c20e99685f at flows:Assistant:mounts:local:c8c19619-89f9-4bce-8f49-b3c20e99685f
[2024-03-22 16:24:52,487][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:24:52,549][aiflows.utils.serve_utils:336][INFO] - Mounted e3948346-eba1-467e-9886-dca4ff06413d at flows:User:mounts:local:e3948346-eba1-467e-9886-dca4ff06413d
[2024-03-22 16:24:52,591][aiflows.utils.serve_utils:336][INFO] - Mounted 28b40997-5206-4a1c-b1a2-687b18a13874 at flows:ChatHumanFlowModule:mounts:local:28b40997-5206-4a1c-b1a2-687b18a13874
[2024-03-22 16:24:52,594][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:24:52,602][aiflows.base_flows.abstract:

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy_ChatHumanFlowModule                                                                                  
├── description
│   └── Proxy of ChatHumanFlowModule                                                                               
├── user_id
│   └── local                                                                                                      
├── flow_id
│   └── 28b40997-5206-4a1c-b1a2-687b18a13874                                                                       
└── flow_endpoint
    └── ChatHumanFlowModule                                                                                        

[2024-03-22 16:24:52,628][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `Proxy_ChatHumanFlowModule` --> `unknown` ~~~
{
    "message_id": "b4c18750-6794-4c71-87c4-6577bc6187c9",
    "created_at": "2024-03-22 15:24:52.627998000",
    "message_type": "FlowMessage",
    "created_by": "Proxy_ChatHumanFlowModule",
    "data": {
        "id": 0,
        "query": "I want to ask you a few questions"
    },
    "src_flow_id": "28b40997-5206-4a1c-b1a2-687b18a13874",
    "reply_data": {
        "mode": "no_reply"
    },
    "src_flow": "Proxy_ChatHumanFlowModule",
    "dst_flow": "unknown",
    "input_message_id": "b4c18750-6794-4c71-87c4-6577bc6187c9",
    "is_reply": false,
    "user_id": "023215d6d023f802cc4d5a91d06aad92f44c33a70ab8f0802995ac74381732dcab"
}
[2024-03-22 16:24:52,653][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ ResetMessageNamespaceOnly (UpdateMessage_NamespaceReset): `Proxy_ChatHumanFlowModule` ~~~
{
    "message_id": "30974a53-25cb-4b6d-99e9-e07be0e81d1b",
 

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Assistantflow                                                                                              
├── description
│   └── A flow that represents the assistant.                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow                                                         
├── flow_endpoint
│   └── Assistant                                                                                                  
├── user_id
│   └── local                                                                                                      
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── input_interface_non_initialized
│   └── []                                                                                                         
└── flow_id
    └── c8c19619-89f9-4bce-8f49-b3c20e99685f                                                                       

...

[2024-03-22 16:25:13,536][aiflows.workers.dispatch_worker:188][INFO] - Input message source: User
[2024-03-22 16:25:13,539][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `User` --> `e3948346-eba1-467e-9886-dca4ff06413d` ~~~
{
    "message_id": "f0686737-7e46-457f-98fe-fa37b601e8ce",
    "created_at": "2024-03-22 15:25:13.395227000",
    "message_type": "FlowMessage",
    "created_by": "User",
    "data": {
        "api_output": "The average speed of a flying swallow (specifically the European Swallow) is approximately 11 meters per second, or about 40 kilometers per hour."
    },
    "src_flow_id": "28b40997-5206-4a1c-b1a2-687b18a13874",
    "reply_data": {
        "mode": "push",
        "user_id": "023215d6d023f802cc4d5a91d06aad92f44c33a70ab8f0802995ac74381732dcab",
        "flow_id": "28b40997-5206-4a1c-b1a2-687b18a13874",
        "input_msg_path": "push_tasks:eb0659ae-3085-4066-a29e-c3d6e5d7c48d:msg"
    },
    "src_flow": "User",
    "dst_flow": "e3948346-eba1-467e-

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Assistantflow                                                                                              
├── description
│   └── A flow that represents the assistant.                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow                                                         
├── flow_endpoint
│   └── Assistant                                                                                                  
├── user_id
│   └── local                                                                                                      
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── input_interface_non_initialized
│   └── []                                                                                                         
└── flow_id
    └── c8c19619-89f9-4bce-8f49-b3c20e99685f                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── User                                                                                                       
├── description
│   └── A flow that represents the user.                                                                           
├── flow_class_name
│   └── flow_modules.aiflows.HumanStandardInputFlowModule.HumanStandardInputFlow                                   
├── flow_endpoint
│   └── User                                                                                                       
├── user_id
│   └── local                                                                                                      
├── request_multi_line_input_flag
│   └── False                                                                                                      
├── query_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': '{{api_output}}\n\nTo end an Interaction, t
├── input_interface
│   └── ['api_output']                                                                                             
├── output_interface
│   └── ['human_input']                                                                                            
└── flow_id
    └── e3948346-eba1-467e-9886-dca4ff06413d                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── ChatInteractiveFlow                                                                                        
├── description
│   └── Flow that enables chatting between a ChatAtomicFlow and a user providing the input.                        
├── _target_
│   └── flow_modules.aiflows.ChatInteractiveFlowModule.ChatHumanFlowModule.instantiate_from_default_config         
├── max_rounds
│   └── 20                                                                                                         
├── input_interface
│   └── ['query']                                                                                                  
├── output_interface
│   └── ['end_of_interaction', 'user_inputs', 'assistant_outputs']                                                 
├── regex_first_occurrence_extractor
│   └── {'regex': '(?<=```answer)([\\s\\S]*?)(?=```)', 'input_key': 'query', 'output_key': 'answer', 'strip': True,
├── end_of_interaction
│   └── {'end_of_interaction_string': '<END>', 'input_key': 'query', 'output_key': 'end_of_interaction'}           
├── subflows_config
│   └── {'Assistant': {'name': 'Assistantflow', 'description': 'A flow that represents the assistant.', 'flow_class
└── flow_id
    └── 28b40997-5206-4a1c-b1a2-687b18a13874                                                                       

[2024-03-22 16:25:17,984][aiflows.utils.serve_utils:242][INFO] - Deleted flow instance 28b40997-5206-4a1c-b1a2-687b18a13874.
~~~~~~Reply~~~~~~
{'user_inputs': ["What's the average speed of a flying swallow ?", '<END>'], 'assistant_outputs': ['Hello! How can I assist you today?', 'The average speed of a flying swallow (specifically the European Swallow) is approximately 11 meters per second, or about 40 kilometers per hour.'], 'end_of_interaction': True}


In [12]:
# Example for ChatWithDemonstrationsFlowModule
flow = "ChatWithDemonstrationsFlowModule"
data = {"id": 0, "question": "What's the capital of France?"}  # This can be a list of samples
run_flow(flow, data, api_information)

[2024-03-22 16:25:53,231][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/CompositeFlow.yaml.
[2024-03-22 16:25:53,276][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.


[2024-03-22 16:25:53,357][aiflows.utils.serve_utils:336][INFO] - Mounted a2a4e4b6-f2f8-4c30-8b88-a22ad09382d7 at flows:DemonstrationsAtomicFlow:mounts:local:a2a4e4b6-f2f8-4c30-8b88-a22ad09382d7
[2024-03-22 16:25:53,370][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:25:53,418][aiflows.utils.serve_utils:336][INFO] - Mounted e266a61f-788a-4bec-928a-440f3e048ab5 at flows:ChatAtomicFlow:mounts:local:e266a61f-788a-4bec-928a-440f3e048ab5
[2024-03-22 16:25:53,447][aiflows.utils.serve_utils:336][INFO] - Mounted 6ee0e264-b245-4fa6-901a-2ee404ec8c86 at flows:ChatWithDemonstrationsFlow:mounts:local:6ee0e264-b245-4fa6-901a-2ee404ec8c86
[2024-03-22 16:25:53,448][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:25:53,5

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy_ChatWithDemonstrationsFlow                                                                           
├── description
│   └── Proxy of ChatWithDemonstrationsFlow                                                                        
├── user_id
│   └── local                                                                                                      
├── flow_id
│   └── 6ee0e264-b245-4fa6-901a-2ee404ec8c86                                                                       
└── flow_endpoint
    └── ChatWithDemonstrationsFlow                                                                                 

[2024-03-22 16:25:53,753][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `Proxy_ChatWithDemonstrationsFlow` --> `unknown` ~~~
{
    "message_id": "b5c11ee3-a25e-4583-9bfc-9782f178032a",
    "created_at": "2024-03-22 15:25:53.753379000",
    "message_type": "FlowMessage",
    "created_by": "Proxy_ChatWithDemonstrationsFlow",
    "data": {
        "id": 0,
        "question": "What's the capital of France?"
    },
    "src_flow_id": "6ee0e264-b245-4fa6-901a-2ee404ec8c86",
    "reply_data": {
        "mode": "no_reply"
    },
    "src_flow": "Proxy_ChatWithDemonstrationsFlow",
    "dst_flow": "unknown",
    "input_message_id": "b5c11ee3-a25e-4583-9bfc-9782f178032a",
    "is_reply": false,
    "user_id": "023215d6d023f802cc4d5a91d06aad92f44c33a70ab8f0802995ac74381732dcab"
}
[2024-03-22 16:25:53,777][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ ResetMessageNamespaceOnly (UpdateMessage_NamespaceReset): `Proxy_ChatWithDemonstrationsFlow` ~~~
{
    "message_id": "821fab53-6f9d

[2024-03-22 16:25:53,791][aiflows.workers.dispatch_worker:119][INFO] - 
~~~ Dispatch task ~~~
[2024-03-22 16:25:53,800][aiflows.workers.dispatch_worker:161][INFO] - flow_endpoint: ChatWithDemonstrationsFlow
[2024-03-22 16:25:53,801][aiflows.workers.dispatch_worker:162][INFO] - flow_id: 6ee0e264-b245-4fa6-901a-2ee404ec8c86
[2024-03-22 16:25:53,805][aiflows.workers.dispatch_worker:163][INFO] - owner_id: local
[2024-03-22 16:25:53,807][aiflows.workers.dispatch_worker:164][INFO] - message_paths: ['push_tasks:bdde6e48-8fc3-45c0-8b2d-f22846d3060b:msg']
[2024-03-22 16:25:53,813][aiflows.workers.dispatch_worker:165][INFO] - parallel_dispatch: False

[2024-03-22 16:25:53,860][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/CompositeFlow.yaml.
[2024-03-22 16:25:53,879][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/a

...

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── True                                                                                                       
├── _target_
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow.instantiate_from_default_config                         
├── name
│   └── proxy SimpleQA_Flow                                                                                        
├── description
│   └── A flow that answers questions                                                                              
├── n_api_retries
│   └── 6                                                                                                          
├── wait_time_between_retries
│   └── 20                                                                                                         
├── system_name
│   └── system                                                                                                     
├── user_name
│   └── user                                                                                                       
├── assistant_name
│   └── assistant                                                                                                  
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── system_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'You are a helpful chatbot that truthfully 
├── init_human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'Answer the following question: {{question}
├── human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': '{{query}}', 'input_variables': ['query']} 
├── input_interface_initialized
│   └── ['query']                                                                                                  
├── query_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt'}                                                        
├── previous_messages
│   └── {'first_k': None, 'last_k': None}                                                                          
├── output_interface
│   └── ['api_output']                                                                                             
├── flow_class_name
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow                                                         
├── input_interface_non_initialized
│   └── ['question']                                                                                               
└── flow_id
    └── e266a61f-788a-4bec-928a-440f3e048ab5                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── flow_class_name
│   └── flow_modules.aiflows.ChatWithDemonstrationsFlowModule.DemonstrationsAtomicFlow                             
├── flow_endpoint
│   └── DemonstrationsAtomicFlow                                                                                   
├── user_id
│   └── local                                                                                                      
├── name
│   └── proxy of DemonstrationsAtomicFlow                                                                          
├── description
│   └── A flow that answers questions with demonstrations                                                          
├── data
│   └── [{'query_data': {'query': 'What is the capital of Turkey?'}, 'response_data': {'response': 'Istambul, my si
├── query_prompt_template
│   └── {'template': 'Answer the following question: {{query}}', 'input_variables': ['query']}                     
├── response_prompt_template
│   └── {'template': '{{response}}', 'input_variables': ['response']}                                              
└── flow_id
    └── a2a4e4b6-f2f8-4c30-8b88-a22ad09382d7                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── proxy SimpleQA_Flow                                                                                        
├── description
│   └── A flow that answers questions                                                                              
├── flow_class_name
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow                                                         
├── flow_endpoint
│   └── ChatAtomicFlow                                                                                             
├── user_id
│   └── local                                                                                                      
├── input_interface_non_initialized
│   └── ['question']                                                                                               
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── n_api_retries
│   └── 6                                                                                                          
├── wait_time_between_retries
│   └── 20                                                                                                         
├── system_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'You are a helpful chatbot that truthfully 
├── init_human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'Answer the following question: {{question}
└── flow_id
    └── e266a61f-788a-4bec-928a-440f3e048ab5                                                                       

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── SimpleQA_Flow_with_Demonstrations                                                                          
├── description
│   └── A sequential flow that answers questions with demonstrations                                               
├── _target_
│   └── flow_modules.aiflows.ChatWithDemonstrationsFlowModule.ChatWithDemonstrationsFlow.instantiate_from_default_c
├── subflows_config
│   └── {'demonstration_flow': {'flow_class_name': 'flow_modules.aiflows.ChatWithDemonstrationsFlowModule.Demonstra
├── input_interface
│   └── ['questions']                                                                                              
├── output_interface
│   └── ['answer']                                                                                                 
└── flow_id
    └── 6ee0e264-b245-4fa6-901a-2ee404ec8c86                                                                       

[2024-03-22 16:25:56,397][aiflows.utils.serve_utils:242][INFO] - Deleted flow instance 6ee0e264-b245-4fa6-901a-2ee404ec8c86.
~~~~~~Reply~~~~~~
{'answer': 'Paris, my sir.'}


In [13]:
# Example for VisionFlowModule
flow = "VisionFlowModule"
url_image = {"type": "url",
            "image": "https://upload.wikimedia.org/wikipedia/commons/thumb/d/dd/Gfp-wisconsin-madison-the-nature-boardwalk.jpg/2560px-Gfp-wisconsin-madison-the-nature-boardwalk.jpg"}
data = {"id": 0, "query": "What’s in this image?", "data": {"images": [url_image]}}  # This can be a list of samples
run_flow(flow, data, api_information)

[2024-03-22 16:26:08,323][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.


[2024-03-22 16:26:08,401][aiflows.utils.serve_utils:336][INFO] - Mounted 3e820a83-022e-41dd-88cd-6ad74b30dbb4 at flows:VisionAtomicFlow:mounts:local:3e820a83-022e-41dd-88cd-6ad74b30dbb4
[2024-03-22 16:26:08,402][aiflows.base_flows.abstract:193][DEBUG] - Flow config not found at /Users/nicolasbaldwin/Documents/OneDrive/EPFL/DLAB/aiflow-colink/aiflows/aiflows/base_flows/AtomicFlow.yaml.
[2024-03-22 16:26:08,431][aiflows.base_flows.abstract:95][DEBUG] - Flow Proxy_VisionAtomicFlow instantiated with the following parameters:


CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── False                                                                                                      
├── name
│   └── Proxy_VisionAtomicFlow                                                                                     
├── description
│   └── Proxy of VisionAtomicFlow                                                                                  
├── user_id
│   └── local                                                                                                      
├── flow_id
│   └── 3e820a83-022e-41dd-88cd-6ad74b30dbb4                                                                       
└── flow_endpoint
    └── VisionAtomicFlow                                                                                           

[2024-03-22 16:26:08,592][aiflows.base_flows.abstract:392][DEBUG] - 
 ~~~ FlowMessage: `Proxy_VisionAtomicFlow` --> `unknown` ~~~
{
    "message_id": "ccbdf245-08e8-4edc-9177-7e75de09a105",
    "created_at": "2024-03-22 15:26:08.592242000",
    "message_type": "FlowMessage",
    "created_by": "Proxy_VisionAtomicFlow",
    "data": {
        "id": 0,
        "query": "What\u2019s in this image?",
        "data": {
            "images": [
                {
                    "type": "url",
                    "image": "https://upload.wikimedia.org/wikipedia/commons/thumb/d/dd/Gfp-wisconsin-madison-the-nature-boardwalk.jpg/2560px-Gfp-wisconsin-madison-the-nature-boardwalk.jpg"
                }
            ]
        }
    },
    "src_flow_id": "3e820a83-022e-41dd-88cd-6ad74b30dbb4",
    "reply_data": {
        "mode": "no_reply"
    },
    "src_flow": "Proxy_VisionAtomicFlow",
    "dst_flow": "unknown",
    "input_message_id": "ccbdf245-08e8-4edc-9177-7e75de09a105",
    "is_reply": false,

CONFIG
├── private_keys
│   └── []                                                                                                         
├── keys_to_ignore_for_hash_flow_config
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_flow_state
│   └── ['name', 'description', 'api_keys', 'api_information', 'private_keys']                                     
├── keys_to_ignore_for_hash_input_data
│   └── []                                                                                                         
├── clear_flow_namespace_on_run_end
│   └── True                                                                                                       
├── enable_cache
│   └── True                                                                                                       
├── _target_
│   └── flow_modules.aiflows.ChatFlowModule.ChatAtomicFlow.instantiate_from_default_config                         
├── name
│   └── Demo Vision Flow                                                                                           
├── description
│   └── A flow that, given a textual input, and a set of images and/or videos, generates a textual output.         
├── n_api_retries
│   └── 6                                                                                                          
├── wait_time_between_retries
│   └── 20                                                                                                         
├── system_name
│   └── system                                                                                                     
├── user_name
│   └── user                                                                                                       
├── assistant_name
│   └── assistant                                                                                                  
├── backend
│   └── {'_target_': 'aiflows.backends.llm_lite.LiteLLMBackend', 'api_infos': [{'_target_': 'aiflows.backends.api_i
├── system_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': 'You are a helpful chatbot that truthfully 
├── init_human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': '{{query}}', 'input_variables': ['query'], 
├── human_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt', 'template': '{{query}}', 'input_variables': ['query']} 
├── input_interface_initialized
│   └── ['query', 'data']                                                                                          
├── query_message_prompt_template
│   └── {'_target_': 'aiflows.prompt_template.JinjaPrompt'}                                                        
├── previous_messages
│   └── {'first_k': None, 'last_k': None}                                                                          
├── output_interface
│   └── ['api_output']                                                                                             
├── input_interface
│   └── ['query', 'data']                                                                                          
├── input_interface_non_initialized
│   └── ['question', 'data']                                                                                       
└── flow_id
    └── 3e820a83-022e-41dd-88cd-6ad74b30dbb4                                                                       

[2024-03-22 16:26:23,833][aiflows.utils.serve_utils:242][INFO] - Deleted flow instance 3e820a83-022e-41dd-88cd-6ad74b30dbb4.
~~~~~~Reply~~~~~~
{'api_output': 'The image shows a wooden boardwalk extending through a lush green meadow. The boardwalk provides a path that allows people to walk through the area without disturbing the natural grasses and plants. The meadow is surrounded by various greenery, including grasses, shrubs, and trees in the distance. Above, the sky is partly cloudy with blue skies and soft white clouds, suggesting a pleasant day. The scene is peaceful and natural, likely a place for outdoor recreation or conservation.'}
